These are screens are those that I follow from: *What Works on Wall Street, Fourth Edition: The Classic Guide to the Best-Performing Investment Strategies of All Time.* 

This is just my interpretation of the books material.

**This material is not intended to be relied upon as a forecast, research or investment advice, and is not a recommendation. Past performance is not always indicative of future returns. I may or may not own stocks listed**

# R System Prep

Data was downloaded the day that I run this notebook. Data should be 1 market day old.

This sheet was run on: 

In [1]:
Sys.time()

[1] "2022-04-20 12:49:22 PDT"

First initialize R environment:

In [2]:
suppressPackageStartupMessages(library(tidyverse))
suppressPackageStartupMessages(library(tidyquant))
suppressPackageStartupMessages(library(rio))
suppressPackageStartupMessages(library(knitr))
suppressPackageStartupMessages(library(kableExtra))
suppressPackageStartupMessages(library(IRdisplay))
#library(kableExtra)

<!-- TEASER_END -->
Read Data

In [3]:
#setwd("D:/OneDrive/SITES/www.michaelghens.com/Rdocs")
universe <-
  read.csv(
    "STOCKS.TXT",
    header = FALSE,
    stringsAsFactors = FALSE,
    na.strings = '-9999999999.990'
  )

universe_names <-
  read.csv(
    "STOCKS_KEY.TXT",
    header = FALSE,
    stringsAsFactors = FALSE,
    na.strings = '-9999999999.990'
  )

names(universe) <- universe_names[, 2]
count1 <- nrow(universe)[1]

Fields imported:

In [4]:
universe_names[, 2] %>%
  kbl("html") %>%
  as.character() %>%
  display_html()

x 
 
 
 
 
 Ticker 
 
 
 Company name 
 
 
 Price Change 52 week 
 
 
 Yield 
 
 
 Sector 
 
 
 Industry 
 
 
 Exchange 
 
 
 ADR/ADS Stock 
 
 
 Market Cap Q1 
 
 
 Price Change 13 week 
 
 
 Price Change 26 week 
 
 
 Cash flow/share 12m 
 
 
 Shares Average Q1 
 
 
 Sales 12m 
 
 
 Buyback Yield 
 
 
 Price/Book 
 
 
 PE 
 
 
 Price/Sales 
 
 
 Enterprise Value/EBITDA 
 
 
 Price/CFPS 
 
 
 Shareholder Yield 
 
 
 1yr chg debt 
 
 
 External Financing 
 
 
 LT Debt/equity Q1 
 
 
 LT debt/free cash flow 12m 
 
 
 EarningsQuality

Fields:

* EarningsQuality: ([Cash from operations 12m]-[Net income 12m])/[Market Cap Q1]
* 1yr chg debt: [Long-term debt Q1]-[Long-term debt Q5])/[Long-term debt Q5]
* External Financing: [Cash from financing Q1]/[Total assets Q1]

Are caculated fields


To clean up the universe of stocks, they must:

* have a ticker
* market cap
* 13,26,52 week price change
* not be over the counter
* not an ADR stock
* not be a reit stock.
* not be a closed end fund (TBA)

In [5]:
universe <- universe[complete.cases(universe$Ticker),]
universe <- universe[complete.cases(universe$`Market Cap Q1`),]
universe <- universe[complete.cases(universe$`Price Change 13 week`),]
universe <- universe[complete.cases(universe$`Price Change 26 week`),]
universe <- universe[complete.cases(universe$`Price Change 52 week`),]
#exchanges
condition <- c("N - New York", "A - American", "M - Nasdaq")
universe <- filter(universe, Exchange %in% condition)
universe <- filter(universe,`ADR/ADS Stock` == 'FALSE')
universe <- filter(universe,!grepl('REITs',Industry))
count2 <- nrow(universe)[1]

# Market Cap Variables

Screens need some market cap and momentom constants

* Minimum deflated Market Cap all cap universe
* Mediam 13 and 26 Momentom for bear trap
* Average Market cap for large cap universe

Calculating deflator, mins, means and medians.

In [6]:
options("getSymbols.warning4.0"=FALSE)
#find inflation Market Cap 150 @ 1995
getSymbols("CPIAUCSL", src = "FRED", auto.assign=getOption('getSymbols.auto.assign',TRUE))
deflator  <-
  last(Cl(to.yearly(CPIAUCSL)))[[1]] / Cl(to.yearly(CPIAUCSL))['1995'][[1]]
mincap <- 150 * deflator
median13w <- median(universe$`Price Change 13 week`)
median26w <- median(universe$`Price Change 26 week`)
avgmcap <- mean(universe$`Market Cap Q1`,  na.rm = TRUE)
avgshares <- mean(universe$`Shares Average Q1`,  na.rm = TRUE)
avgcashflowshares <- mean(universe$`Cash flow/share 12m`,  na.rm = TRUE)
avgsales15 <- mean(universe$`Sales 12m`,  na.rm = TRUE) * 1.5

[1] "CPIAUCSL"

# Create stock unverses

Screens are based on thre inverses of stocks 

* smallstocks
* allstocks
* largestocks
* marketleaders

## Create means and medians 

In [7]:
smallstocks <- filter(universe, `Market Cap Q1` <= avgmcap & `Market Cap Q1` >= mincap)

allstocks <- filter(universe, `Market Cap Q1` >= mincap)

largestocks <- filter(universe, `Market Cap Q1` >= avgmcap)

marketleaders <- allstocks %>% filter(Sector != "59  - Utilities") %>% 
  filter(`Shares Average Q1` > avgshares) %>%
  filter(`Cash flow/share 12m` > avgcashflowshares) %>%
  filter(`Sales 12m` > avgsales15)

Function to add rankings

In [8]:
calcvc2 <- function(x) {
  #Calculate VC2
  #subtract ntile from 101 to reverse (correct) Order. So Small is big
  x$`Price/Book.Rank` <-
    100 - round(percent_rank(x$`Price/Book`) * 100, 1)
  x$PE.Rank <- 100 - round(percent_rank(x$PE) * 100, 1)
  x$`Price/Sales.Rank` <-
    100 - round(percent_rank(x$`Price/Sales`) * 100, 1)
  x$`Enterprise Value/EBITDA.Rank` <-
    100 - round(percent_rank(x$`Enterprise Value/EBITDA`) * 100, 1)
  x$`Price/CFPS.Rank` <-
    100 - round(percent_rank(x$`Price/CFPS`) * 100, 1)
  x$`Shareholder Yield.Rank` <-
    round(percent_rank(x$`Shareholder Yield`) * 100, 1)
  
  #Stocks with no rank get 50
  x$`Price/Book.Rank`[is.na(x$`Price/Book.Rank`)] <- 50
  x$PE.Rank[is.na(x$PE.Rank)] <- 50
  x$`Price/Sales.Rank`[is.na(x$`Price/Sales.Rank`)] <- 50
  x$`Enterprise Value/EBITDA.Rank`[is.na(x$`Enterprise Value/EBITDA.Rank`)] <-
    50
  x$`Price/CFPS.Rank`[is.na(x$`Price/CFPS.Rank`)] <- 50
  x$`Shareholder Yield.Rank`[is.na(x$`Shareholder Yield.Rank`)] <- 50
  #Sum the Ranks
  x$SumRank <-
    x$`Price/Book.Rank` + x$PE.Rank + x$`Price/Sales.Rank` + x$`Enterprise Value/EBITDA.Rank` + x$`Price/CFPS.Rank` + x$`Shareholder Yield.Rank`
  x$VC2 <- round(percent_rank(x$SumRank) * 100, 1)
  return(x)
}

allstocks <- calcvc2(allstocks)
largestocks <- calcvc2(largestocks)
marketleaders <- calcvc2(marketleaders)

# Portfolios

## Trending Value

In [9]:
TrendingValue <- allstocks %>%  filter(VC2 >= 90) %>% arrange(desc(`Price Change 26 week`)) %>% slice_head(n = 25) %>% select(Ticker, `Company name`,Sector,Industry)

TrendingValue %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 OBE 
 Obsidian Energy Ltd 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 TGL 
 TransGlobe Energy Corporation 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 GRIN 
 Grindrod Shipping Holdings Ltd 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 TMST 
 Timkensteel Corp 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 RYI 
 Ryerson Holding Corp 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 X 
 United States Steel Corporatio 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 BTE 
 Baytex Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 NUE 
 Nucor Corporation 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 QUAD 
 Quad/Graphics, Inc. 
 52 - Industrials 
 52203020 - Commercial Printing Services 
 
 
 CNX 
 CNX Resources Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 ZEUS 
 Olympic Steel, Inc. 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 MERC 
 Mercer International Inc. 
 51 - Basic Materials 
 51301020 - Paper Products 
 
 
 STLD 
 Steel Dynamics, Inc. 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 CHK 
 Chesapeake Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 TECK.B 
 Teck Resources Ltd 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 CMC 
 Commercial Metals Company 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 GNK 
 Genco Shipping & Trading Limit 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 VHI 
 Valhi, Inc. 
 51 - Basic Materials 
 51101030 - Chemicals - Specialty 
 
 
 VIRT 
 Virtu Financial Inc 
 55 - Financials 
 55102050 - Financial & Commodity Market Operators & Service Provi 
 
 
 NGD 
 New Gold Inc (USA) 
 51 - Basic Materials 
 51201060 - Metals & Mining - Gold 
 
 
 SBLK 
 Star Bulk Carriers Corp. 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 SPLP 
 Steel Partners Holdings LP 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 DDS 
 Dillard's, Inc. 
 53 - Consumer Cyclicals 
 53402010 - Retailers - Department Stores 
 
 
 ARLP 
 Alliance Resource Partners, L. 
 50 - Energy 
 50101010 - Coal

## Cheap Stocks on the mend

In [10]:
cheapmend <-
  allstocks %>%  filter(VC2 >= 70) %>% filter(`Price Change 13 week` > median13w) %>% filter(`Price Change 26 week` >
                                        median26w) %>% arrange(desc(`Price Change 26 week`)) %>%             
                                        slice_head(n = 25) %>% select(Ticker, `Company name`)

cheapmend %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 
 
 
 
 AMR 
 Alpha Metallurgical Resources 
 
 
 OBE 
 Obsidian Energy Ltd 
 
 
 EGY 
 VAALCO Energy, Inc. 
 
 
 TRQ 
 Turquoise Hill Resources Ltd 
 
 
 VET 
 Vermilion Energy Inc 
 
 
 GTE 
 Gran Tierra Energy Inc 
 
 
 PBF 
 PBF Energy Inc 
 
 
 BATL 
 Battalion Oil Corp 
 
 
 TGA 
 TransGlobe Energy Corporation 
 
 
 TGL 
 TransGlobe Energy Corporation 
 
 
 GRIN 
 Grindrod Shipping Holdings Ltd 
 
 
 TMST 
 Timkensteel Corp 
 
 
 RYI 
 Ryerson Holding Corp 
 
 
 ANDE 
 Andersons Inc 
 
 
 CAR 
 Avis Budget Group Inc. 
 
 
 CNR 
 Cornerstone Building Brands In 
 
 
 X 
 United States Steel Corporatio 
 
 
 BTE 
 Baytex Energy Corp 
 
 
 NUE 
 Nucor Corporation 
 
 
 AAV 
 Advantage Energy Ltd 
 
 
 NRP 
 Natural Resource Partners LP 
 
 
 QUAD 
 Quad/Graphics, Inc. 
 
 
 ARCH 
 Arch Resources Inc 
 
 
 CNX 
 CNX Resources Corp 
 
 
 APA 
 APA Corp (US)

## Market Leaders

### Price Appreciation

In [11]:
mlsy <- marketleaders %>% filter(`Price Change 13 week` > median13w) %>% 
  filter(`Price Change 26 week` >median26w) %>% 
  arrange(desc(`Shareholder Yield`)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
mlsy %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 PRU 
 Prudential Financial Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 AMGN 
 Amgen, Inc. 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 SCCO 
 Southern Copper Corp 
 51 - Basic Materials 
 51201050 - Metals & Mining - Specialty 
 
 
 IP 
 International Paper Co 
 51 - Basic Materials 
 51302020 - Paper Packaging 
 
 
 WMB 
 Williams Companies Inc 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 PSX 
 Phillips 66 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 ADP 
 Automatic Data Processing Inc 
 57 - Technology 
 57201010 - IT Services & Consulting 
 
 
 VLO 
 Valero Energy Corporation 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 CTVA 
 Corteva Inc 
 54 - Consumer Non-Cyclicals 
 54102010 - Fishing & Farming 
 
 
 EMR 
 Emerson Electric Co. 
 52 - Industrials 
 52102030 - Electrical Components & Equipment 
 
 
 IPG 
 Interpublic Group of Companies 
 53 - Consumer Cyclicals 
 53302010 - Advertising & Marketing 
 
 
 TXN 
 Texas Instruments Incorporated 
 57 - Technology 
 57101010 - Semiconductors 
 
 
 TSN 
 Tyson Foods, Inc. 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 AA 
 Alcoa Corp 
 51 - Basic Materials 
 51201030 - Metals & Mining - Aluminum 
 
 
 CINF 
 Cincinnati Financial Corporati 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 FISV 
 Fiserv Inc 
 52 - Industrials 
 52203040 - Business Support Services 
 
 
 MCD 
 McDonald's Corp 
 53 - Consumer Cyclicals 
 53301020 - Restaurants & Bars 
 
 
 UNH 
 UnitedHealth Group Inc 
 56 - Healthcare 
 56102020 - Managed Health care 
 
 
 ABT 
 Abbott Laboratories 
 56 - Healthcare 
 56101020 - Medical Equipment, Supplies & Distribution 
 
 
 MSI 
 Motorola Solutions Inc 
 57 - Technology 
 57102010 - Communications & Networking 
 
 
 EOG 
 EOG Resources Inc 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production

In [12]:
mlvc2 <- marketleaders %>% filter(`Price Change 13 week` > median13w) %>% 
  filter(`Price Change 26 week` >median26w) %>% 
  arrange(desc(VC2)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
mlvc2 %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 PRU 
 Prudential Financial Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 PARA 
 Paramount Global 
 53 - Consumer Cyclicals 
 53302020 - Broadcasting 
 
 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 X 
 United States Steel Corporatio 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 TECK.B 
 Teck Resources Ltd 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 TSN 
 Tyson Foods, Inc. 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 IP 
 International Paper Co 
 51 - Basic Materials 
 51302020 - Paper Packaging 
 
 
 TECK 
 Teck Resources Ltd (USA) 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 CINF 
 Cincinnati Financial Corporati 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 IPG 
 Interpublic Group of Companies 
 53 - Consumer Cyclicals 
 53302010 - Advertising & Marketing 
 
 
 ADM 
 Archer-Daniels-Midland Co 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 NWSA 
 News Corp 
 53 - Consumer Cyclicals 
 53302040 - Consumer Publishing 
 
 
 CVS 
 CVS Health Corp 
 56 - Healthcare 
 56102010 - Healthcare Facilities & Services 
 
 
 UAL 
 United Airlines Holdings Inc 
 52 - Industrials 
 52406010 - Airlines 
 
 
 VLO 
 Valero Energy Corporation 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 BAM.A 
 Brookfield Asset Management In 
 55 - Financials 
 55102020 - Investment Management & Fund Operators 
 
 
 CNC 
 Centene Corp 
 56 - Healthcare 
 56102020 - Managed Health care 
 
 
 EOG 
 EOG Resources Inc 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 PSX 
 Phillips 66 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 CTVA 
 Corteva Inc 
 54 - Consumer Non-Cyclicals 
 54102010 - Fishing & Farming 
 
 
 RJF 
 Raymond James Financial, Inc. 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 AA 
 Alcoa Corp 
 51 - Basic Materials 
 51201030 - Metals & Mining - Aluminum

In [13]:
unique(arrange(rbind(mlvc2,mlsy),Ticker)) %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 1 
 AA 
 Alcoa Corp 
 51 - Basic Materials 
 51201030 - Metals & Mining - Aluminum 
 
 
 3 
 ABT 
 Abbott Laboratories 
 56 - Healthcare 
 56101020 - Medical Equipment, Supplies & Distribution 
 
 
 4 
 ADM 
 Archer-Daniels-Midland Co 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 5 
 ADP 
 Automatic Data Processing Inc 
 57 - Technology 
 57201010 - IT Services & Consulting 
 
 
 6 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 8 
 AMGN 
 Amgen, Inc. 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 9 
 BAM.A 
 Brookfield Asset Management In 
 55 - Financials 
 55102020 - Investment Management & Fund Operators 
 
 
 10 
 CINF 
 Cincinnati Financial Corporati 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 12 
 CNC 
 Centene Corp 
 56 - Healthcare 
 56102020 - Managed Health care 
 
 
 13 
 CTVA 
 Corteva Inc 
 54 - Consumer Non-Cyclicals 
 54102010 - Fishing & Farming 
 
 
 15 
 CVS 
 CVS Health Corp 
 56 - Healthcare 
 56102010 - Healthcare Facilities & Services 
 
 
 16 
 EMR 
 Emerson Electric Co. 
 52 - Industrials 
 52102030 - Electrical Components & Equipment 
 
 
 17 
 EOG 
 EOG Resources Inc 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 19 
 FISV 
 Fiserv Inc 
 52 - Industrials 
 52203040 - Business Support Services 
 
 
 20 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 22 
 IP 
 International Paper Co 
 51 - Basic Materials 
 51302020 - Paper Packaging 
 
 
 24 
 IPG 
 Interpublic Group of Companies 
 53 - Consumer Cyclicals 
 53302010 - Advertising & Marketing 
 
 
 26 
 MCD 
 McDonald's Corp 
 53 - Consumer Cyclicals 
 53301020 - Restaurants & Bars 
 
 
 27 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 29 
 MSI 
 Motorola Solutions Inc 
 57 - Technology 
 57102010 - Communications & Networking 
 
 
 30 
 NWSA 
 News Corp 
 53 - Consumer Cyclicals 
 53302040 - Consumer Publishing 
 
 
 31 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 33 
 PARA 
 Paramount Global 
 53 - Consumer Cyclicals 
 53302020 - Broadcasting 
 
 
 34 
 PRU 
 Prudential Financial Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 36 
 PSX 
 Phillips 66 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 38 
 RJF 
 Raymond James Financial, Inc. 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 39 
 SCCO 
 Southern Copper Corp 
 51 - Basic Materials 
 51201050 - Metals & Mining - Specialty 
 
 
 40 
 TECK 
 Teck Resources Ltd (USA) 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 41 
 TECK.B 
 Teck Resources Ltd 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 42 
 TSN 
 Tyson Foods, Inc. 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 44 
 TXN 
 Texas Instruments Incorporated 
 57 - Technology 
 57101010 - Semiconductors 
 
 
 45 
 UAL 
 United Airlines Holdings Inc 
 52 - Industrials 
 52406010 - Airlines 
 
 
 46 
 UNH 
 UnitedHealth Group Inc 
 56 - Healthcare 
 56102020 - Managed Health care 
 
 
 47 
 VLO 
 Valero Energy Corporation 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 49 
 WMB 
 Williams Companies Inc 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 50 
 X 
 United States Steel Corporatio 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel

In [14]:
utilities <- allstocks %>%
  filter(Sector == "59  - Utilities") %>%
  arrange(desc(VC2)) %>%
  slice_head(n =25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
  
noncyc <- filter(allstocks,Sector == "54  - Consumer Non-Cyclicals") %>%
  arrange(desc(`Shareholder Yield`)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
  
arrange(rbind(utilities,noncyc),Ticker)   %>%
  kable("html") %>%
  as.character() %>%
  display_html()

constap <- rbind(slice_head(noncyc,n=3),slice_head(utilities,n=3))

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 AES 
 AES Corp 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 AGRO 
 Adecoagro SA 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 ALE 
 ALLETE Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 CAH 
 Cardinal Health Inc 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 CLX 
 Clorox Co 
 54 - Consumer Non-Cyclicals 
 54201010 - Household Products 
 
 
 COKE 
 Coca-Cola Consolidated Inc 
 54 - Consumer Non-Cyclicals 
 54101030 - Non-Alcoholic Beverages 
 
 
 CSV 
 Carriage Services, Inc. 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 ETR 
 Entergy Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 EVRG 
 Evergy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 EXC 
 Exelon Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 FTS 
 Fortis Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 HAIN 
 Hain Celestial Group Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 HE 
 Hawaiian Electric Industries, 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 HLF 
 Herbalife Nutrition Ltd 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 HRB 
 H & R Block Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 KEN 
 Kenon Holdings Ltd 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 KR 
 Kroger Co 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 MCK 
 McKesson Corporation 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 MDU 
 Mdu Resources Group Inc 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 MED 
 Medifast Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 MIC 
 Macquarie Infrastructure Holdi 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 MO 
 Altria Group Inc 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 NFG 
 National Fuel Gas Co. 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 NJR 
 New Jersey Resources Corp 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 NRG 
 NRG Energy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 NUS 
 Nu Skin Enterprises, Inc. 
 54 - Consumer Non-Cyclicals 
 54201020 - Personal Products 
 
 
 NWN 
 Northwest Natural Holding Co 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 OGE 
 OGE Energy Corp. 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 OTTR 
 Otter Tail Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PCG 
 PG&E Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PG 
 Procter & Gamble Co 
 54 - Consumer Non-Cyclicals 
 54201020 - Personal Products 
 
 
 PM 
 Philip Morris International In 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 PNW 
 Pinnacle West Capital Corporat 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 POR 
 Portland General Electric Comp 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 POST 
 Post Holdings Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 PPL 
 PPL Corp 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 PRG 
 PROG Holdings Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 SCI 
 Service Corporation Internatio 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 SENEA 
 Seneca Foods Corp 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 SFM 
 Sprouts Farmers Market Inc 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 SJM 
 J M Smucker Co 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 TAC 
 TransAlta Corporation (USA) 
 59 - Utilities 
 59101020 - Utilities - Independent Power Producers 
 
 
 TR 
 Tootsie Roll Industries, Inc. 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 UGI 
 UGI Corp 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 USNA 
 USANA Health Sciences, Inc. 

## My 24 stock port

In [15]:
n <-1
c <-1
while(c < 12)  {
  mlC <- unique(rbind(slice_head(mlvc2,n=n),slice_head(mlsy,n=n)))
  n <- n + 1
  c = nrow(mlC)
}

n <-1
c <-1
rportTemp <- rbind(slice_head(mlC, n=6),constap)
while(c < 25)  {

rport <- unique(rbind(rportTemp,slice_head(TrendingValue,n=n)))
  n <- n + 1
  c = nrow(rport)
}
rport %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 1 
 PRU 
 Prudential Financial Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 2 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 3 
 PARA 
 Paramount Global 
 53 - Consumer Cyclicals 
 53302020 - Broadcasting 
 
 
 4 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 5 
 X 
 United States Steel Corporatio 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 6 
 TECK.B 
 Teck Resources Ltd 
 51 - Basic Materials 
 51201080 - Metals & Mining - Diversified 
 
 
 7 
 VLGEA 
 Village Super Market, Inc. 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 8 
 COKE 
 Coca-Cola Consolidated Inc 
 54 - Consumer Non-Cyclicals 
 54101030 - Non-Alcoholic Beverages 
 
 
 9 
 HLF 
 Herbalife Nutrition Ltd 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 10 
 NRG 
 NRG Energy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 11 
 UGI 
 UGI Corp 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 12 
 VIA 
 Via Renewables Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 13 
 OBE 
 Obsidian Energy Ltd 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 14 
 TGL 
 TransGlobe Energy Corporation 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 15 
 GRIN 
 Grindrod Shipping Holdings Ltd 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 16 
 TMST 
 Timkensteel Corp 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 17 
 RYI 
 Ryerson Holding Corp 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 19 
 BTE 
 Baytex Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 20 
 NUE 
 Nucor Corporation 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 21 
 QUAD 
 Quad/Graphics, Inc. 
 52 - Industrials 
 52203020 - Commercial Printing Services 
 
 
 22 
 CNX 
 CNX Resources Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 23 
 ZEUS 
 Olympic Steel, Inc. 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 24 
 MERC 
 Mercer International Inc. 
 51 - Basic Materials 
 51301020 - Paper Products 
 
 
 25 
 STLD 
 Steel Dynamics, Inc. 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 27 
 CHK 
 Chesapeake Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production